In [1]:
import numpy as np                                             
from numpy import sqrt, dot, cross                       
from numpy.linalg import norm 
import math
import paho.mqtt.client as mqtt
import time

In [2]:
def calibrate_argons(Distance1_2,Distance2_3,Distance3_1):
    ''' takes in the distances between the 3 base argons and returns a array of each argons relative position with argon one being at (0,0,0) '''
    Angle_1 = math.acos((Distance3_1^2+Distance1_2^2-Distance2_3^2)/(2*Distance3_1*Distance1_2)) #side side side formula
    return np.array([[0,0,0],[Distance2_3,0,0],[Distance3_1(math.cos(Angle_1)),Distance3_1(math.sin(Angle_1)),0]])


In [3]:
def trilaterate(P1,P2,P3,r1,r2,r3):   
    ''' Takes in Each base Argons (x,y,z) cordinates and distance from the tracked argon and outputs the relative location of the tracked Argon '''                   
    temp1 = P2-P1                                        
    e_x = temp1/norm(temp1)                              
    temp2 = P3-P1                                        
    i = dot(e_x,temp2)                                   
    temp3 = temp2 - i*e_x                                
    e_y = temp3/norm(temp3)                              
    e_z = cross(e_x,e_y)                                 
    d = norm(P2-P1)                                      
    j = dot(e_y,temp2)                                   
    x = (r1*r1 - r2*r2 + d*d) / (2*d)                    
    y = (r1*r1 - r3*r3 -2*i*x + i*i + j*j) / (2*j)       
    temp4 = r1*r1 - x*x - y*y                            
    if temp4<0:                                          
        return np.asarray([0,0,0])
    z = sqrt(temp4)                                      
    p_12_a = P1 + x*e_x + y*e_y + abs(z*e_z)                            
    return p_12_a 

In [6]:
#Incoming data storage

Argon1_distance = -1
Argon2_distance = 100
Argon3_distance = 100

ArgonT_Acceleration = (0,0,0)


In [18]:
#TOPICS
A1_RSSI = "BAR/argon1/RSSI"
A2_RSSI = "BAR/argon1/RSSI"
A3_RSSI = "BAR/argon1/RSSI"

AT_ACCL_X = "BAR/argonT/accel/x"
AT_ACCL_Y = "BAR/argonT/accel/Y"
AT_ACCL_X = "BAR/argonT/accel/Z"

In [7]:
# Callback function when a message is received from the MQTT broker
def on_message(client, userdata, msg):
    global Argon1_distance 
    global Argon2_distance 
    global Argon3_distance
    topic = msg.topic
    message = int(msg.payload.decode())
    #distance = 0.01308*(math.exp(-0.07207*(message)))-0.1636
    if topic == A1_RSSI:
        Argon1_distance = message
    elif topic == A2_RSSI:
        Argon2_distance = message
    elif topic == A3_RSSI:
        Argon3_distance = message

In [19]:
def on_connect(client, userdata, flags, rc):

    client.subscribe(A1_RSSI)
    client.subscribe(A2_RSSI)
    client.subscribe(A3_RSSI)

    client.subscribe(AT_ACCL_X)
    client.subscribe(AT_ACCL_Y)
    client.subscribe(AT_ACCL_Z)

In [9]:

broker = "lab.thewcl.com"
port = 1883
client = mqtt.Client()

client.on_connect = on_connect
client.on_message = on_message

client.connect(broker, port)

0

In [17]:
# Connect to the MQTT broker
client.connect(broker, port)
client.loop_start()

#argon_locations = calibrate_argons(64,64,64)
locations = []

a1 = []
while True:
    #print(Argon1_distance ,Argon2_distance,Argon3_distance)
    locations.append(trilaterate(np.asarray([0,0,0]),np.asarray([80,0,0]),np.asarray([40,69,0]),Argon1_distance ,Argon2_distance,Argon3_distance))
    #print(Argon1_distance ,Argon2_distance,Argon3_distance)
    locations.append([Argon1_distance ,Argon2_distance,Argon3_distance])
    if len(locations) > 500:
        print(sum([locations[-idx][0] for idx in range(0,500)])/500,sum([locations[-idx][1] for idx in range(0,500)])/500,sum([locations[-idx][2] for idx in range(0,500)])/500)
    #if Argon1_distance != -1:
    #    a1.append(Argon1_distance)
    #    print(sum(a1)/len(a1))
    #print(locations[-1])
    #print(Argon1_distance)
    time.sleep(0.01)



# Publish a message to the MQTT topic
#client.publish("BAR/Argon1/Brodcast", True)





# Disconnect from the MQTT broker


-15.201387499999985 -24.591355072463745 -9.065396663377902
-15.219637499999985 -24.60773188405795 -9.059170529463696
-15.237887499999983 -24.624108695652154 -9.052944395549492
-15.256137499999982 -24.640485507246353 -9.046718261635286
-15.274387499999982 -24.656862318840563 -9.040492127721082
-15.292637499999982 -24.673239130434766 -9.034265993806878
-15.310887499999982 -24.68961594202897 -9.02803985989267
-15.329137499999982 -24.70599275362317 -9.021813725978468
-15.34738749999998 -24.722369565217374 -9.015587592064263
-15.36563749999998 -24.738746376811577 -9.00936145815006
-15.38388749999998 -24.755123188405783 -9.003135324235854
-15.40213749999998 -24.771499999999985 -8.996909190321652
-15.42038749999998 -24.787876811594188 -8.990683056407448
-15.438637499999981 -24.804253623188394 -8.984456922493244
-15.456887499999983 -24.820630434782593 -8.97823078857904
-15.475137499999983 -24.837007246376796 -8.972004654664836
-15.493387499999983 -24.853384057971002 -8.965778520750634
-15.5116

KeyboardInterrupt: 

In [12]:
#client.loop_stop()
#client.disconnect()

0

In [ ]:
0.01308*(math.exp(-0.07207*(-80)))-0.1636

4.010626480671998

In [ ]:

#import sys
#!{sys.executable} -m pip install paho-mqtt
#!conda install --yes --prefix {sys.prefix} paho-mqtt



Received message: tijdskfjlkjsddsaReceived message: tijdskfjlkjsddsaReceived message: tijdskfjlkjsddsa
None
Received message: tijdskfjlkjsddsa

testtopic



Solving environment: ...working... failed with initial frozen solve. Retrying with flexible solve.
Solving environment: ...working... failed with initial frozen solve. Retrying with flexible solve.



PackagesNotFoundError: The following packages are not available from current channels:

  - paho-mqtt

Current channels:

  - https://repo.anaconda.com/pkgs/main/win-64
  - https://repo.anaconda.com/pkgs/main/noarch
  - https://repo.anaconda.com/pkgs/r/win-64
  - https://repo.anaconda.com/pkgs/r/noarch
  - https://repo.anaconda.com/pkgs/msys2/win-64
  - https://repo.anaconda.com/pkgs/msys2/noarch

To search for alternate channels that may provide the conda package you're
looking for, navigate to

    https://anaconda.org

and use the search bar at the top of the page.




Connected to MQTT broker with result code 0
